# Modeling

In [2]:
import numpy as np
import pandas as pd
pd.options.display.max_columns=None

import matplotlib.pyplot as plt
import seaborn as sns

import joblib

In [3]:
import sklearn
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import ExtraTreeClassifier, DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier

import mlflow
from mlflow import sklearn

In [4]:
mlflow.set_tracking_uri("./mlruns/")
mlflow.set_experiment("Titanic")

<Experiment: artifact_location='./mlruns/1', creation_time=None, experiment_id='1', last_update_time=None, lifecycle_stage='active', name='Titanic', tags={}>

In [5]:
train_df = joblib.load('trainset.csv')
test_df = joblib.load('testset.csv')

In [6]:
from sklearn.model_selection import train_test_split
train_df, val_df = train_test_split(train_df, test_size=0.2, stratify=train_df['Survived'], shuffle=True)

In [7]:
train_df.shape, val_df.shape, test_df.shape

((712, 17), (179, 17), (418, 16))

In [8]:
train_df.columns

Index(['Survived', 'Pclass', 'Sex', 'Age', 'SibSp', 'Parch', 'Fare', 'Family',
       'Age_band', 'Alone', 'Fare_cat', 'Initial_1', 'Initial_2', 'Initial_3',
       'Initial_4', 'Embarked_1', 'Embarked_2'],
      dtype='object')

In [9]:
NUMERIC_FEATURES = [
    'Age', 'SibSp', 'Parch', 'Fare', 'Family', 
]

CATEGORICAL_FEATURES = [
    'Pclass', 'Sex', 'Age_band', 'Alone', 'Fare_cat', 'Initial_1', 'Initial_2', 'Initial_3',
       'Initial_4', 'Embarked_1', 'Embarked_2'
]

LABEL = 'Survived'
FEATURES = NUMERIC_FEATURES + CATEGORICAL_FEATURES

In [10]:
X_train, y_train = train_df[FEATURES], train_df[LABEL]
X_val, y_val = val_df[FEATURES], val_df[LABEL]
X_test = test_df

In [11]:
from sklearn.preprocessing import StandardScaler

ss_scaler = StandardScaler()

X_train[NUMERIC_FEATURES] = ss_scaler.fit_transform(X_train[NUMERIC_FEATURES]).copy()
X_val[NUMERIC_FEATURES] = ss_scaler.transform(X_val[NUMERIC_FEATURES]).copy()
X_test[NUMERIC_FEATURES] = ss_scaler.transform(X_test[NUMERIC_FEATURES]).copy()

/tmp/ipykernel_4888/1875920493.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X_train[NUMERIC_FEATURES] = ss_scaler.fit_transform(X_train[NUMERIC_FEATURES]).copy()
/tmp/ipykernel_4888/1875920493.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  X_val[NUMERIC_FEATURES] = ss_scaler.transform(X_val[NUMERIC_FEATURES]).copy()


In [12]:
from sklearn.metrics import accuracy_score

In [14]:
models = [
    [LogisticRegression(), { 'penalty' : 'l2', 'C' : 1,}],
    [SVC(), {'C' : 1, 'kernel' : 'rbf',}],
    [KNeighborsClassifier(),{'n_neighbors' : 5,}],
    [DecisionTreeClassifier(),{'max_depth' : None, 'random_state' : 42,}],
    [ExtraTreeClassifier(),{'max_depth' : None, 'random_state' : 42,}],
    [RandomForestClassifier(), {'max_depth' : None, 'random_state' : 42,}],
    [AdaBoostClassifier(),{'n_estimators' : 50, 'random_state' : 42,}],
    [XGBClassifier(), {'max_depth' : None, 'random_state' : 42,}],
    [LGBMClassifier(),{'max_depth' : None, 'random_state' : 42, }],
    [CatBoostClassifier(),{'max_depth' : None, 'random_state' : 42, }],
]

In [15]:
def mlflow_run_sklearn(
    run_name,
    tags,
    model_params,
    model,
    X_train,
    y_train,
    X_val=None,
    y_val=None,
):
    with mlflow.start_run(run_name=run_name):
        model.set_params(**model_params)
        model.fit(X_train, y_train)
        y_pred = model.predict(X_val)
        acc = accuracy_score(y_val, y_pred)
        
        print(f"{run_name} : {acc}")
        
        mlflow.set_tags(tags)
        mlflow.log_params(model_params)
        mlflow.log_metric('acc', acc)
        mlflow.sklearn.log_model(model, 'sk_models')

In [ ]:
for model_name, (model, model_params) in zip([
    'lr', 'svc', 'knn', 'dt', 'et', 'rf', 'ab', 'xgb', 'lgbm', 'cb'
], models):
    mlflow_run_sklearn(
        run_name=model_name + "_baseline",
        tags={
            'model_name' : model_name,
        },
        model_params=model_params,
        model=model,
        X_train=X_train,
        y_train=y_train,
        X_val=X_val,
        y_val=y_val
    )

# 5. Hyper parameter tuning

In [1]:
import optuna

In [ ]:
CatBoostClassifier()

In [16]:
def objective(trial:optuna.Trial):
    param = {
        "objective": trial.suggest_categorical("objective", ["Logloss", "CrossEntropy"]),
        "colsample_bylevel": trial.suggest_float("colsample_bylevel", 0.01, 0.1, log=True),
        "depth": trial.suggest_int("depth", 4, 10),
        "boosting_type": trial.suggest_categorical("boosting_type", ["Ordered", "Plain"]),
        "bootstrap_type": trial.suggest_categorical(
            "bootstrap_type", ["Bayesian", "Bernoulli", "MVS"]
        ),
        "eval_metric": "Accuracy",
    }
    if param["bootstrap_type"] == "Bayesian":
        param["bagging_temperature"] = trial.suggest_float("bagging_temperature", 0, 10)
    elif param["bootstrap_type"] == "Bernoulli":
        param["subsample"] = trial.suggest_float("subsample", 0.1, 1, log=True)
        
    gbm = CatBoostClassifier(**param)
    
    gbm.fit(X_train, y_train, verbose=1)
    y_pred = gbm.predict(X_val)
    
    acc = accuracy_score(y_val, y_pred)
    return acc


    
study = optuna.create_study(
    pruner=optuna.pruners.MedianPruner(n_warmup_steps=5), direction="maximize"
)
study.optimize(objective, n_trials=100, timeout=600)



[I 2023-04-21 10:53:01,930] A new study created in memory with name: no-name-ec2e3856-fd50-4b93-8caf-aed3ed967b5f


Learning rate set to 0.008911
0:	learn: 0.6882022	total: 76.5ms	remaining: 1m 16s
1:	learn: 0.7106742	total: 77ms	remaining: 38.4s
2:	learn: 0.7219101	total: 77.5ms	remaining: 25.8s
3:	learn: 0.7078652	total: 77.9ms	remaining: 19.4s
4:	learn: 0.7191011	total: 78.5ms	remaining: 15.6s
5:	learn: 0.7500000	total: 79.1ms	remaining: 13.1s
6:	learn: 0.7696629	total: 79.5ms	remaining: 11.3s
7:	learn: 0.7724719	total: 79.9ms	remaining: 9.91s
8:	learn: 0.7584270	total: 80.2ms	remaining: 8.83s
9:	learn: 0.7542135	total: 80.7ms	remaining: 7.99s
10:	learn: 0.7598315	total: 81.1ms	remaining: 7.29s
11:	learn: 0.7542135	total: 81.5ms	remaining: 6.71s
12:	learn: 0.7837079	total: 82.2ms	remaining: 6.24s
13:	learn: 0.7837079	total: 82.5ms	remaining: 5.81s
14:	learn: 0.7808989	total: 82.9ms	remaining: 5.44s
15:	learn: 0.7865169	total: 83.5ms	remaining: 5.13s
16:	learn: 0.7837079	total: 83.9ms	remaining: 4.85s
17:	learn: 0.7837079	total: 84.2ms	remaining: 4.6s
18:	learn: 0.7837079	total: 84.8ms	remaining: 

[I 2023-04-21 10:53:03,472] Trial 0 finished with value: 0.8044692737430168 and parameters: {'objective': 'Logloss', 'colsample_bylevel': 0.05928908238267016, 'depth': 4, 'boosting_type': 'Plain', 'bootstrap_type': 'MVS'}. Best is trial 0 with value: 0.8044692737430168.


Learning rate set to 0.008911
0:	learn: 0.6165730	total: 14.1ms	remaining: 14.1s
1:	learn: 0.6165730	total: 15.4ms	remaining: 7.67s
2:	learn: 0.6165730	total: 16.4ms	remaining: 5.45s
3:	learn: 0.6165730	total: 17.5ms	remaining: 4.36s
4:	learn: 0.6165730	total: 18.6ms	remaining: 3.69s
5:	learn: 0.6165730	total: 19.7ms	remaining: 3.26s
6:	learn: 0.6165730	total: 20.7ms	remaining: 2.94s
7:	learn: 0.6165730	total: 21.7ms	remaining: 2.7s
8:	learn: 0.6165730	total: 22.8ms	remaining: 2.51s
9:	learn: 0.6165730	total: 23.8ms	remaining: 2.35s
10:	learn: 0.6165730	total: 24.9ms	remaining: 2.24s
11:	learn: 0.6165730	total: 26.3ms	remaining: 2.16s
12:	learn: 0.6165730	total: 28.8ms	remaining: 2.19s
13:	learn: 0.6165730	total: 30.3ms	remaining: 2.13s
14:	learn: 0.6165730	total: 31.3ms	remaining: 2.05s
15:	learn: 0.6165730	total: 32.3ms	remaining: 1.99s
16:	learn: 0.6165730	total: 33.3ms	remaining: 1.93s
17:	learn: 0.6165730	total: 34.4ms	remaining: 1.88s
18:	learn: 0.6165730	total: 35.5ms	remaining:

[I 2023-04-21 10:53:04,925] Trial 1 finished with value: 0.776536312849162 and parameters: {'objective': 'Logloss', 'colsample_bylevel': 0.023151186258822874, 'depth': 8, 'boosting_type': 'Ordered', 'bootstrap_type': 'Bernoulli', 'subsample': 0.7377319212817055}. Best is trial 0 with value: 0.8044692737430168.


...

[I 2023-04-21 10:55:43,266] Trial 97 finished with value: 0.8100558659217877 and parameters: {'objective': 'CrossEntropy', 'colsample_bylevel': 0.08954372021095702, 'depth': 7, 'boosting_type': 'Plain', 'bootstrap_type': 'MVS'}. Best is trial 51 with value: 0.8268156424581006.


0:	learn: 0.6221910	total: 1.14ms	remaining: 1.14s
1:	learn: 0.7907303	total: 2.75ms	remaining: 1.37s
2:	learn: 0.7865169	total: 3.98ms	remaining: 1.32s
3:	learn: 0.8005618	total: 5.15ms	remaining: 1.28s
4:	learn: 0.7949438	total: 6.28ms	remaining: 1.25s
5:	learn: 0.7752809	total: 7.39ms	remaining: 1.22s
6:	learn: 0.7710674	total: 8.51ms	remaining: 1.21s
7:	learn: 0.7092697	total: 9.97ms	remaining: 1.24s
8:	learn: 0.7823034	total: 20.5ms	remaining: 2.26s
9:	learn: 0.7626404	total: 21.9ms	remaining: 2.16s
10:	learn: 0.7949438	total: 30.4ms	remaining: 2.73s
11:	learn: 0.8005618	total: 33.6ms	remaining: 2.76s
12:	learn: 0.7879213	total: 35ms	remaining: 2.65s
13:	learn: 0.8089888	total: 38.2ms	remaining: 2.69s
14:	learn: 0.8089888	total: 40.3ms	remaining: 2.65s
15:	learn: 0.8075843	total: 42.7ms	remaining: 2.62s
16:	learn: 0.8061798	total: 46.7ms	remaining: 2.7s
17:	learn: 0.7935393	total: 48.9ms	remaining: 2.67s
18:	learn: 0.7907303	total: 49.9ms	remaining: 2.58s
19:	learn: 0.7977528	tota

[I 2023-04-21 10:55:45,055] Trial 98 finished with value: 0.8100558659217877 and parameters: {'objective': 'CrossEntropy', 'colsample_bylevel': 0.05528061195360677, 'depth': 8, 'boosting_type': 'Ordered', 'bootstrap_type': 'MVS'}. Best is trial 51 with value: 0.8268156424581006.


0:	learn: 0.6699438	total: 1.47ms	remaining: 1.46s
1:	learn: 0.7317416	total: 3.43ms	remaining: 1.71s
2:	learn: 0.7331461	total: 4.92ms	remaining: 1.63s
3:	learn: 0.8061798	total: 6.88ms	remaining: 1.71s
4:	learn: 0.8019663	total: 8.29ms	remaining: 1.65s
5:	learn: 0.7696629	total: 9.6ms	remaining: 1.59s
6:	learn: 0.7738764	total: 18.4ms	remaining: 2.61s
7:	learn: 0.8202247	total: 21.2ms	remaining: 2.63s
8:	learn: 0.8061798	total: 22.7ms	remaining: 2.5s
9:	learn: 0.8174157	total: 24.9ms	remaining: 2.46s
10:	learn: 0.8103933	total: 26.4ms	remaining: 2.37s
11:	learn: 0.8146067	total: 29.4ms	remaining: 2.42s
12:	learn: 0.8160112	total: 31.9ms	remaining: 2.42s
13:	learn: 0.8258427	total: 36ms	remaining: 2.53s
14:	learn: 0.8384831	total: 40.3ms	remaining: 2.65s
15:	learn: 0.8398876	total: 43.2ms	remaining: 2.65s
16:	learn: 0.8370787	total: 44.8ms	remaining: 2.59s
17:	learn: 0.8384831	total: 46.1ms	remaining: 2.51s
18:	learn: 0.8314607	total: 48.9ms	remaining: 2.53s
19:	learn: 0.8441011	total

[I 2023-04-21 10:55:47,115] Trial 99 finished with value: 0.8100558659217877 and parameters: {'objective': 'CrossEntropy', 'colsample_bylevel': 0.09467816486251894, 'depth': 6, 'boosting_type': 'Ordered', 'bootstrap_type': 'MVS'}. Best is trial 51 with value: 0.8268156424581006.


In [17]:
print("Number of finished trials: {}".format(len(study.trials)))

print("Best trial:")
trial = study.best_trial

print("  Value: {}".format(trial.value))

print("  Params: ")
for key, value in trial.params.items():
    print("    {}: {}".format(key, value))

Number of finished trials: 100
Best trial:
  Value: 0.8268156424581006
  Params: 
    objective: CrossEntropy
    colsample_bylevel: 0.06749555944129286
    depth: 6
    boosting_type: Ordered
    bootstrap_type: MVS


In [20]:
import mlflow
logged_model = 'runs:/6f2f6bdbe3274a869dc80088b9c30ee5/sk_models'

loaded_model = mlflow.pyfunc.load_model(logged_model)

y_test = loaded_model.predict(X_test)

In [21]:
submission = pd.read_csv("test.csv").loc[:, ['PassengerId']]
submission['Survived'] = y_test

In [22]:
submission.to_csv("submission.csv", index=False)